##Implementation of CNN using CIFAR10 dataset:

In [2]:
import tensorflow as tf
from tensorflow.keras import layers, models
from tensorflow.keras.datasets import cifar10
from tensorflow.keras.utils import to_categorical

# Load and preprocess the data
(train_images, train_labels), (test_images, test_labels) = cifar10.load_data()
train_images, test_images = train_images / 255.0, test_images / 255.0
train_labels = to_categorical(train_labels)
test_labels = to_categorical(test_labels)

# Building the model
model = models.Sequential([
    layers.Conv2D(32, (3, 3), activation='relu', input_shape=(32, 32, 3)),
    layers.MaxPooling2D((2, 2)),
    layers.Conv2D(64, (3, 3), activation='relu'),
    layers.MaxPooling2D((2, 2)),
    layers.Conv2D(64, (3, 3), activation='relu'),
    layers.Flatten(),
    layers.Dense(64, activation='relu'),
    layers.Dense(10, activation='softmax')
])

# Compile the model
model.compile(optimizer='adam',
              loss='categorical_crossentropy',
              metrics=['accuracy'])

# Train the model
model.fit(train_images, train_labels, epochs=25, validation_data=(test_images, test_labels))

# Evaluate the model
test_loss, test_acc = model.evaluate(test_images, test_labels)
print(f"Test accuracy: {test_acc:.4f}")


170498071/170498071 ━━━━━━━━━━━━━━━━━━━━ 5s 0us/step


/usr/local/lib/python3.10/dist-packages/keras/src/layers/convolutional/base_conv.py:107: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)


Epoch 1/25
1563/1563 ━━━━━━━━━━━━━━━━━━━━ 79s 49ms/step - accuracy: 0.3598 - loss: 1.7262 - val_accuracy: 0.5467 - val_loss: 1.2804
Epoch 2/25
1563/1563 ━━━━━━━━━━━━━━━━━━━━ 80s 48ms/step - accuracy: 0.5811 - loss: 1.1753 - val_accuracy: 0.6229 - val_loss: 1.0608
Epoch 3/25
1563/1563 ━━━━━━━━━━━━━━━━━━━━ 82s 48ms/step - accuracy: 0.6430 - loss: 1.0078 - val_accuracy: 0.6645 - val_loss: 0.9583
Epoch 4/25
1563/1563 ━━━━━━━━━━━━━━━━━━━━ 83s 49ms/step - accuracy: 0.6875 - loss: 0.8901 - val_accuracy: 0.6881 - val_loss: 0.9008
Epoch 5/25
1563/1563 ━━━━━━━━━━━━━━━━━━━━ 80s 48ms/step - accuracy: 0.7181 - loss: 0.8051 - val_accuracy: 0.7056 - val_loss: 0.8598
Epoch 6/25
1563/1563 ━━━━━━━━━━━━━━━━━━━━ 86s 50ms/step - accuracy: 0.7469 - loss: 0.7237 - val_accuracy: 0.7053 - val_loss: 0.8538
Epoch 7/25
1563/1563 ━━━━━━━━━━━━━━━━━━━━ 79s 49ms/step - accuracy: 0.7620 - loss: 0.6760 - val_accuracy: 0.6886 - val_loss: 0.9045
Epoch 8/25
1563/1563 ━━━━━━━━━━━━━━━━━━━━ 82s 49ms/step - accuracy: 0.7814 -

##Implementation of CNN using CIFAR10 dataset with Ray:


In [2]:
pip install ray

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 66.8/66.8 MB 11.7 MB/s eta 0:00:00


In [5]:
#!/usr/bin/env python
# -*- coding: utf-8 -*-
"""Train keras CNN on the CIFAR10 small images dataset.

The model comes from: https://zhuanlan.zhihu.com/p/29214791,
and it gets to about 87% validation accuracy in 100 epochs.

Note that the script requires a machine with 4 GPUs. You
can set {"gpu": 0} to use CPUs for training, although
it is less efficient.
"""

import argparse
import numpy as np
import tensorflow as tf
import time
from tensorflow.keras.datasets import cifar10
from tensorflow.keras.layers import (
    Convolution2D,
    Dense,
    Dropout,
    Flatten,
    Input,
    MaxPooling2D,
)
from tensorflow.keras.models import Model, load_model
from tensorflow.keras.preprocessing.image import ImageDataGenerator

from ray import train, tune
from ray.tune import Trainable
from ray.tune.schedulers import PopulationBasedTraining

num_classes = 10
NUM_SAMPLES = 128


class Cifar10Model(Trainable):
    def _read_data(self):
        # The data, split between train and test sets:
        (x_train, y_train), (x_test, y_test) = cifar10.load_data()

        # Convert class vectors to binary class matrices.
        y_train = tf.keras.utils.to_categorical(y_train, num_classes)
        y_test = tf.keras.utils.to_categorical(y_test, num_classes)

        x_train = x_train.astype("float32")
        x_train /= 255
        x_test = x_test.astype("float32")
        x_test /= 255

        return (x_train, y_train), (x_test, y_test)

    def _build_model(self, input_shape):
        x = Input(shape=(32, 32, 3))
        y = x
        y = Convolution2D(
            filters=64,
            kernel_size=3,
            strides=1,
            padding="same",
            activation="relu",
            kernel_initializer="he_normal",
        )(y)
        y = Convolution2D(
            filters=64,
            kernel_size=3,
            strides=1,
            padding="same",
            activation="relu",
            kernel_initializer="he_normal",
        )(y)
        y = MaxPooling2D(pool_size=2, strides=2, padding="same")(y)

        y = Convolution2D(
            filters=128,
            kernel_size=3,
            strides=1,
            padding="same",
            activation="relu",
            kernel_initializer="he_normal",
        )(y)
        y = Convolution2D(
            filters=128,
            kernel_size=3,
            strides=1,
            padding="same",
            activation="relu",
            kernel_initializer="he_normal",
        )(y)
        y = MaxPooling2D(pool_size=2, strides=2, padding="same")(y)

        y = Convolution2D(
            filters=256,
            kernel_size=3,
            strides=1,
            padding="same",
            activation="relu",
            kernel_initializer="he_normal",
        )(y)
        y = Convolution2D(
            filters=256,
            kernel_size=3,
            strides=1,
            padding="same",
            activation="relu",
            kernel_initializer="he_normal",
        )(y)
        y = MaxPooling2D(pool_size=2, strides=2, padding="same")(y)

        y = Flatten()(y)
        y = Dropout(self.config.get("dropout", 0.5))(y)
        y = Dense(units=10, activation="softmax", kernel_initializer="he_normal")(y)

        model = Model(inputs=x, outputs=y, name="model1")
        return model

    def setup(self, config):
        self.train_data, self.test_data = self._read_data()
        x_train = self.train_data[0]
        model = self._build_model(x_train.shape[1:])

        opt = tf.keras.optimizers.Adadelta(
            learning_rate=self.config.get("learning_rate", 1e-4), weight_decay=self.config.get("decay", 1e-4)
        )
        model.compile(
            loss="categorical_crossentropy", optimizer=opt, metrics=["accuracy"]
        )
        self.model = model

    def step(self):
        x_train, y_train = self.train_data
        x_train, y_train = x_train[:NUM_SAMPLES], y_train[:NUM_SAMPLES]
        x_test, y_test = self.test_data
        x_test, y_test = x_test[:NUM_SAMPLES], y_test[:NUM_SAMPLES]

        aug_gen = ImageDataGenerator(
            # set input mean to 0 over the dataset
            featurewise_center=False,
            # set each sample mean to 0
            samplewise_center=False,
            # divide inputs by dataset std
            featurewise_std_normalization=False,
            # divide each input by its std
            samplewise_std_normalization=False,
            # apply ZCA whitening
            zca_whitening=False,
            # randomly rotate images in the range (degrees, 0 to 180)
            rotation_range=0,
            # randomly shift images horizontally (fraction of total width)
            width_shift_range=0.1,
            # randomly shift images vertically (fraction of total height)
            height_shift_range=0.1,
            # randomly flip images
            horizontal_flip=True,
            # randomly flip images
            vertical_flip=False,
        )

        aug_gen.fit(x_train)
        batch_size = self.config.get("batch_size", 64)
        gen = aug_gen.flow(x_train, y_train, batch_size=batch_size)
        self.model.fit(
            x=gen, steps_per_epoch=len(x_train) // batch_size, epochs=self.config.get("epochs", 1), validation_data=(x_test, y_test), verbose=1
        )

        # loss, accuracy
        _, accuracy = self.model.evaluate(x_test, y_test, verbose=0)
        return {"mean_accuracy": accuracy}

    def save_checkpoint(self, checkpoint_dir):
        file_path = checkpoint_dir + "/model.keras"
        self.model.save(file_path)

    def load_checkpoint(self, checkpoint_dir):
        # See https://stackoverflow.com/a/42763323
        del self.model
        file_path = checkpoint_dir + "/model.keras"
        self.model = load_model(file_path)

    def cleanup(self):
        # If need, save your model when exit.
        # saved_path = self.model.save(self.logdir)
        # print("save model at: ", saved_path)
        pass

    def reset_config(self, new_config):
        # Update the model's dropout rate, re-build and recompile if learning rate changes
        if 'dropout' in new_config and new_config['dropout'] != self.config['dropout']:
            self.config['dropout'] = new_config['dropout']
            # If model structure or compilation parameters change, rebuild and recompile the model
            if 'learning_rate' in new_config and new_config['learning_rate'] != self.config['learning_rate']:
                self.config['learning_rate'] = new_config['learning_rate']
                x_train = self.train_data[0]
                self.model = self._build_model(x_train.shape[1:])
                opt = tf.keras.optimizers.Adadelta(
                    learning_rate=self.config['learning_rate'],
                    weight_decay=self.config.get('decay', 1e-4)
                )
                self.model.compile(
                    loss="categorical_crossentropy",
                    optimizer=opt,
                    metrics=["accuracy"]
                )
        return True


if __name__ == "__main__":
    parser = argparse.ArgumentParser()
    parser.add_argument(
        "--smoke-test", action="store_true", help="Finish quickly for testing"
    )
    args, _ = parser.parse_known_args()

    space = {
        "epochs": 25,
        "batch_size": 64,
        "learning_rate": tune.grid_search([10**-4, 10**-2]),
        "decay": tune.sample_from(lambda spec: spec.config.learning_rate / 100.0),
        "dropout": tune.grid_search([0.25, 0.5]),
    }
    if args.smoke_test:
        space["learning_rate"] = 10**-4
        space["dropout"] = 0.5

    perturbation_interval = 20
    pbt = PopulationBasedTraining(
        time_attr="training_iteration",
        perturbation_interval=perturbation_interval,
        hyperparam_mutations={
            "dropout": lambda: np.random.uniform(0, 1),
        },
    )

    # Start timing
    start_time = time.time()

    tuner = tune.Tuner(
        tune.with_resources(
            Cifar10Model,
            resources={"cpu": 2, "gpu": 1},
        ),
        run_config=train.RunConfig(
            name="pbt_cifar10",
            stop={
                "mean_accuracy": 0.80,
                "training_iteration": 30,
            },
            checkpoint_config=train.CheckpointConfig(
                checkpoint_frequency=perturbation_interval,
                checkpoint_score_attribute="mean_accuracy",
                num_to_keep=2,
            ),
        ),
        tune_config=tune.TuneConfig(
            scheduler=pbt,
            num_samples=4,
            metric="mean_accuracy",
            mode="max",
            reuse_actors=True,
        ),
        param_space=space,
    )
    results = tuner.fit()

    # End timing
    end_time = time.time()
    execution_time = end_time - start_time

    print("Best hyperparameters found were: ", results.get_best_result().config)
    print(f"Total execution time: {execution_time:.2f} seconds")

2024-12-11 05:16:23,926	WARNING callback.py:136 -- The TensorboardX logger cannot be instantiated because either TensorboardX or one of it's dependencies is not installed. Please make sure you have the latest version of TensorboardX installed: `pip install -U tensorboardx`
2024-12-11 05:16:23,937	WARNING sample.py:469 -- sample_from functions that take a spec dict are deprecated. Please update your function to work with the config dict directly.
2024-12-11 05:16:23,941	WARNING sample.py:469 -- sample_from functions that take a spec dict are deprecated. Please update your function to work with the config dict directly.
2024-12-11 05:16:23,946	WARNING sample.py:469 -- sample_from functions that take a spec dict are deprecated. Please update your function to work with the config dict directly.
2024-12-11 05:16:23,950	WARNING sample.py:469 -- sample_from functions that take a spec dict are deprecated. Please update your function to work with the config dict directly.
2024-12-11 05:16:23,95

+----------------------------------------------------------+
| Configuration for experiment     pbt_cifar10             |
+----------------------------------------------------------+
| Search algorithm                 BasicVariantGenerator   |
| Scheduler                        PopulationBasedTraining |
| Number of trials                 16                      |
+----------------------------------------------------------+

View detailed results here: /root/ray_results/pbt_cifar10

Trial status: 16 PENDING
Current time: 2024-12-11 05:16:24. Total running time: 0s
Logical resource usage: 0/2 CPUs, 0/1 GPUs (0.0/1.0 accelerator_type:T4)
+-------------------------------------------------------------------+
| Trial name                 status       learning_rate     dropout |
+-------------------------------------------------------------------+
| Cifar10Model_109d6_00000   PENDING             0.0001        0.25 |
| Cifar10Model_109d6_00001   PENDING             0.0001        0.5  |
| Cifar

(pid=103781) 2024-12-11 05:16:26.408944: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:485] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
(pid=103781) 2024-12-11 05:16:26.435243: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:8454] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
(pid=103781) 2024-12-11 05:16:26.442450: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1452] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
(pid=103781) 2024-12-11 05:16:27.851412: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT
(Cifar10Model pid=103781) WARNING: All log messages before absl::InitializeLog() is called are written to STDERR
(Cifar10Model pid=103781) I0000 00:00:1733894191.113368  103781 cuda_executo


Trial Cifar10Model_109d6_00000 started with configuration:
+--------------------------------------------------+
| Trial Cifar10Model_109d6_00000 config            |
+--------------------------------------------------+
| batch_size                                    64 |
| decay                                          0 |
| dropout                                     0.25 |
| epochs                                        25 |
| learning_rate                             0.0001 |
+--------------------------------------------------+
(Cifar10Model pid=103781) Epoch 1/25


(Cifar10Model pid=103781) /usr/local/lib/python3.10/dist-packages/keras/src/trainers/data_adapters/py_dataset_adapter.py:122: UserWarning: Your `PyDataset` class should call `super().__init__(**kwargs)` in its constructor. `**kwargs` can include `workers`, `use_multiprocessing`, `max_queue_size`. Do not pass these arguments to `fit()`, as they will be ignored.
(Cifar10Model pid=103781)   self._warn_if_super_not_called()
(Cifar10Model pid=103781) WARNING: All log messages before absl::InitializeLog() is called are written to STDERR
(Cifar10Model pid=103781) I0000 00:00:1733894194.490460  103854 service.cc:146] XLA service 0x7abe6c0111d0 initialized for platform CUDA (this does not guarantee that XLA will be used). Devices:
(Cifar10Model pid=103781) I0000 00:00:1733894194.490496  103854 service.cc:154]   StreamExecutor device (0): Tesla T4, Compute Capability 7.5
(Cifar10Model pid=103781) I0000 00:00:1733894198.247495  103854 device_compiler.h:188] Compiled cluster using XLA!  This line 

...

(Cifar10Model pid=103781) Checkpoint successfully created at: Checkpoint(filesystem=local, path=/root/ray_results/pbt_cifar10/Cifar10Model_109d6_00014_14_dropout=0.2500,learning_rate=0.0100_2024-12-11_05-16-24/checkpoint_000001)
(Cifar10Model pid=103781) Restored on 172.28.0.12 from checkpoint: Checkpoint(filesystem=local, path=/root/ray_results/pbt_cifar10/Cifar10Model_109d6_00015_15_dropout=0.5000,learning_rate=0.0100_2024-12-11_05-16-24/checkpoint_000000)


(Cifar10Model pid=103781) Epoch 1/25
1/2 ━━━━━━━━━━━━━━━━━━━━ 3s 4s/step - accuracy: 0.3281 - loss: 2.0222
2/2 ━━━━━━━━━━━━━━━━━━━━ 4s 562ms/step - accuracy: 0.2969 - loss: 2.0492 - val_accuracy: 0.1094 - val_loss: 2.3385
(Cifar10Model pid=103781) Epoch 2/25
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step - accuracy: 0.0000e+00 - loss: 0.0000e+00 - val_accuracy: 0.1094 - val_loss: 2.3385
(Cifar10Model pid=103781) Epoch 3/25
1/2 ━━━━━━━━━━━━━━━━━━━━ 0s 100ms/step - accuracy: 0.2031 - loss: 2.1389
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 57ms/step - accuracy: 0.2135 - loss: 2.1284 - val_accuracy: 0.1094 - val_loss: 2.3385
(Cifar10Model pid=103781) Epoch 4/25
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step - accuracy: 0.0000e+00 - loss: 0.0000e+00 - val_accuracy: 0.1094 - val_loss: 2.3385
(Cifar10Model pid=103781) Epoch 5/25
1/2 ━━━━━━━━━━━━━━━━━━━━ 0s 121ms/step - accuracy: 0.2188 - loss: 2.1345
2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 56ms/step - accuracy: 0.2396 - loss: 2.1257 - val_accuracy: 0.1094 - val_loss: 2.3385
(Cifar10Mode

2024-12-11 05:44:18,260	INFO tune.py:1009 -- Wrote the latest version of all result files and experiment state to '/root/ray_results/pbt_cifar10' in 0.0168s.



Trial Cifar10Model_109d6_00015 completed after 30 iterations at 2024-12-11 05:44:18. Total running time: 27min 54s
+---------------------------------------------------+
| Trial Cifar10Model_109d6_00015 result             |
+---------------------------------------------------+
| time_this_iter_s                          3.08786 |
| time_total_s                              106.756 |
| training_iteration                             30 |
| mean_accuracy                             0.10938 |
+---------------------------------------------------+

Trial status: 16 TERMINATED
Current time: 2024-12-11 05:44:18. Total running time: 27min 54s
Logical resource usage: 2.0/2 CPUs, 1.0/1 GPUs (0.0/1.0 accelerator_type:T4)
Current best trial: 109d6_00013 with mean_accuracy=0.109375 and params={'epochs': 25, 'batch_size': 64, 'learning_rate': 0.0001, 'decay': 1e-06, 'dropout': 0.5}
+-------------------------------------------------------------------------------------------------------------+
| Trial 

(Cifar10Model pid=103781) Checkpoint successfully created at: Checkpoint(filesystem=local, path=/root/ray_results/pbt_cifar10/Cifar10Model_109d6_00015_15_dropout=0.5000,learning_rate=0.0100_2024-12-11_05-16-24/checkpoint_000001)
